In [1]:
import torch
import numpy as np
import pandas as pd
import json

from transformers import GPT2LMHeadModel, GPT2Tokenizer
from transformers import TrainingArguments, Trainer
from transformers import DataCollatorForLanguageModeling, TextDataset
from torch.utils.data import Dataset, DataLoader

from peft import get_peft_model, LoraConfig

/Users/alexanderknyshov/Desktop/LLM/Data/venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
device = 'mps'

lora_config = LoraConfig(
    r=16,                       # Ранг, может быть изменен в зависимости от задачи
    lora_alpha=32,             # Гиперпараметр, который можно настроить
    lora_dropout=0.1,          # Вероятность дропаута для LoRA # Модули, которые будут адаптированы
)

model = GPT2LMHeadModel.from_pretrained('ai-forever/rugpt3small_based_on_gpt2').to(device)
model = get_peft_model(model, lora_config)
tokenizer = GPT2Tokenizer.from_pretrained('ai-forever/rugpt3small_based_on_gpt2')

/Users/alexanderknyshov/Desktop/LLM/Data/venv/lib/python3.11/site-packages/peft/tuners/lora/layer.py:1091: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(


In [6]:
with open('/Users/alexanderknyshov/Desktop/LLM/Data/datasets/train_set.json', 'r') as json_file:
    data = json.load(json_file)

def format_text(data, idx, data_format):
    news_text = "Напиши финансовую рекомендацию на основе этого текста новостей: " + " ".join(data['news'][idx])
    recommendation_text = " ".join(data['recommendations'][idx])
    data_format['news'].append(news_text)
    data_format['recommendations'].append(recommendation_text)

In [7]:
train_len = 4000
data_train = {'news': [], 'recommendations': []}
data_val = {'news': [], 'recommendations': []}

for i in range(train_len):
    format_text(data, i, data_train)
for i in range(train_len, len(data['news'])):
    format_text(data, i, data_val)

In [8]:
data_train

{'news': ['Напиши финансовую рекомендацию на основе этого текста новостей: экономическая политическая нестабильность последнего времени привела падению продаж одежды россии сравнению аналогичным периодом прошлого года отмечают эксперты мае года оперируют данными период февраля апреля такое снижение спроса связывают двумя факторами вопервых уходом российского рынка крупных западных сетей массмаркета вовторых вынужденным снижением расходов многих россиянгазпром смирился новый экспортный маршрут северный поток который построен запущен эксплуатацию сможет набрать максимальную скорость поставок голубого топлива европу года срока трубам лучшем случае сможет экспортироваться лишь половина заявленных объемов причем лишь случае соответствующее разрешение даст германияевросоюз полон решимости принять шестой пакет санкций котором конца года предусмотрен полный отказ закупок российской нефти нефтепродуктов мк пообщался экспертами выяснить это выльется бюджета россии валютных поступленийзападные эк

In [5]:
class NewsRecData(Dataset):
    def __init__(self, data, tokenizer, max_length = 1024):
        self.data = data
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.data['news'])
    
    def __getitem__(self, idx):
        input_text = self.data['news'][idx]
        output_text = self.data['recommendations'][idx]

        input_tokens = self.tokenizer.encode(input_text, truncation=True, max_length=self.max_length, return_tensors='pt', padding='max_length').squeeze(0)
        output_tokens = self.tokenizer.encode(output_text, truncation=True, max_length=self.max_length, return_tensors='pt', padding='max_length').squeeze(0)

        return {
            'input_ids': input_tokens,
            'labels': output_tokens
        }
        

In [6]:
train_dataset = NewsRecData(data_train, tokenizer)
validation_dataset = NewsRecData(data_val, tokenizer)

data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer, 
    mlm=False
)

In [7]:
training_args = TrainingArguments(
    output_dir='/Users/alexanderknyshov/Desktop/LLM/Data/model_ft/results',
    per_device_train_batch_size=3,
    per_device_eval_batch_size=3,
    logging_dir='/Users/alexanderknyshov/Desktop/LLM/Data/model_ft/results/logs',
    num_train_epochs=1,
    logging_steps=10,
    save_steps=500,
    save_total_limit=2,
    evaluation_strategy="steps",
    eval_steps=500,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=validation_dataset,
    data_collator=data_collator
)

/Users/alexanderknyshov/Desktop/LLM/Data/venv/lib/python3.11/site-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [8]:
trainer.train()

  1%|          | 10/1334 [00:15<31:55,  1.45s/it] 

{'loss': 6.3055, 'grad_norm': 0.9538859724998474, 'learning_rate': 4.9625187406296854e-05, 'epoch': 0.01}


  1%|▏         | 20/1334 [00:31<32:35,  1.49s/it]

{'loss': 6.1463, 'grad_norm': 2.2198281288146973, 'learning_rate': 4.9250374812593707e-05, 'epoch': 0.01}


  2%|▏         | 30/1334 [00:45<33:02,  1.52s/it]

...

                                                  
 37%|███▋      | 500/1334 [15:10<18:46,  1.35s/it]

{'eval_runtime': 194.0234, 'eval_samples_per_second': 6.066, 'eval_steps_per_second': 2.026, 'epoch': 0.37}


 38%|███▊      | 510/1334 [15:29<57:00,  4.15s/it]   

{'loss': 5.4716, 'grad_norm': 0.9527052640914917, 'learning_rate': 3.088455772113943e-05, 'epoch': 0.38}


KeyboardInterrupt: 

In [3]:
device = 'mps'

model = GPT2LMHeadModel.from_pretrained('/Users/alexanderknyshov/Desktop/LLM/Data/model_ft/results/checkpoint-500').to(device)
tokenizer = GPT2Tokenizer.from_pretrained('ai-forever/rugpt3small_based_on_gpt2')

In [4]:
model.eval()

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50264, 768)
    (wpe): Embedding(2048, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2SdpaAttention(
          (c_attn): lora.Linear(
            (base_layer): Conv1D()
            (lora_dropout): ModuleDict(
              (default): Dropout(p=0.1, inplace=False)
            )
            (lora_A): ModuleDict(
              (default): Linear(in_features=768, out_features=16, bias=False)
            )
            (lora_B): ModuleDict(
              (default): Linear(in_features=16, out_features=2304, bias=False)
            )
            (lora_embedding_A): ParameterDict()
            (lora_embedding_B): ParameterDict()
            (lora_magnitude_vector): ModuleDict()
          )
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dr

In [25]:
def generate_text(prompt, max_length=100, num_return_sequences=1):
    # Токенизация входного текста
    input_ids = tokenizer.encode(prompt, return_tensors='pt').to(device)

    attention_mask = torch.ones(input_ids.shape, device=device)

    # Генерация текста
    with torch.no_grad():
        output = model.generate(
            input_ids,
            #attention_mask=attention_mask,
            max_length=max_length,
            num_return_sequences=num_return_sequences,
            do_sample=True,  # Используйте do_sample для более случайного текста
            top_k=50,  # Используйте top-k sampling
            top_p=0.90,  # Используйте nucleus sampling
            temperature=1.3,  # Устанавливает креативность генерации
            pad_token_id=tokenizer.eos_token_id
        )

    # Декодирование выходных токенов
    return [tokenizer.decode(output[i], skip_special_tokens=True) for i in range(num_return_sequences)]

# Пример использования
prompt = "Напиши финансовую рекомендацию на основе этого текста новостей: Дефицит российского бюджета может сильно вырасти по итогам года"
generated_texts = generate_text(prompt, max_length=128, num_return_sequences=5)

for i, text in enumerate(generated_texts):
    print(f"Generated text {i+1}:\n{text}\n")

Generated text 1:
Напиши финансовую рекомендацию на основе этого текста новостей: Дефицит российского бюджета может сильно вырасти по итогам года - 2015 гг. Минэкономразвития выступило основным препятствием росту бюджетной обеспеченности регионов страны. Из-за дефицита финансов россиян будет сокращено количество запланированных мероприятий госуслуг на 2016 год, сообщили агентству новостей izmgromn.ru в Минэкономразвития России. При этом предполагается, что потребность граждан будет сокращаться в среднем примерно четыре недели подряд: чтобы достигнуть нынешних значений годовой план сократился к середине января этого года менее чем на треть заявил источник в ведомстве отметил рост спроса на услуги мобильной связи оператор сообщает свою пресс-службу m

Generated text 2:
Напиши финансовую рекомендацию на основе этого текста новостей: Дефицит российского бюджета может сильно вырасти по итогам года из-за девальвации рубля, так заявил гендиректор Минфина РФ Сергей Шаталов на совещании по дене